# Força Assíncrona

Nesta seção o equacionamento realizado considerou a aplicação de uma força rotativa assíncrona excitando o sitema conforme proposto no livro texto da disciplina, "Rotordynamics Prediction in Engineering, Second Edition", {cite:ts}`lalanne_rotordynamics_1998`.

Foram calculadas as amplitudes de vibração em função da velocidade de rotação

## Importando módulos e configurando o ambiente

In [1]:
'''
    Bibliotecas de terceira parte
'''
import numpy as np
import plotly.graph_objects as go

'''
    Biblioteca criada para a realização das análises dinâmicas
    no contexto da disciplina
'''
import rotor_analysis as rd

'''
    Configurando pint.Quantity
'''
Q_ = rd.Q_

## Definindo parâmetros

In [2]:
# Material instances and properties
steel = rd.Material(name='Steel',
                    density=Q_(7800, 'kg/m^3'),
                    young_modulus=Q_(2e11,"Pa"))

# Shaft
L = Q_(0.4, 'm')
shaft = rd.Shaft(outer_radius=Q_(0.01, 'm'),
                 inner_radius=Q_(0.0, 'm'),
                 length=L,
                 material=steel)

# Disc
disc = rd.Disc(outer_radius=Q_(0.150, 'm'),
               inner_radius=Q_(0.010, 'm'),
               length=Q_(0.030, 'm'),
               material=steel,
               coordinate=L/3)

# Rotor
rotor = rd.Rotor(shaft, disc)
speed_range = np.linspace(0, 9000, 101)

In [3]:
def A1_async(speed, *args):
    '''Compute the displacemente aplitude of the rotor with an asynchronous 
    excitation.
    
    Args:
        speed (function): Rotational speed in RPM.
        F0 (float): Asynchronous force magnitude
        s (float): A multiplier thats desynchronize the excitation

    Remarks:
        len(args) shall be equals to 2
    '''
    F0, s = args
    k1, k2 = rotor.stiffness
    m = rotor.mass
    spin = speed / 60 * 2 * np.pi
    a = rotor.a
    div = s**2 * (s**2 * m**2 - a**2) * spin**4 - m * (k1 + k2) * s**2 * spin**2 + k1 * k2
    return (k2 - (m * s**2 + a * s) * spin**2) * F0 / div

In [4]:
# Computing the values
values = []
s = 0.5
for speed in speed_range:
    values.append(abs(A1_async(speed, 1, s)))

In [5]:
# Generating the Standard Campbell Diagram
campbell_fig = rotor.plot_Campbell()
data = campbell_fig.to_dict()

new_critical_speed = np.sqrt(rotor.stiffness[0]/(s*(rotor.mass*s - rotor.a))) * 60 / (2 * np.pi)

point_critical_speed = go.Scatter(
    x=[new_critical_speed],
    y=[new_critical_speed / 120],
    mode="markers",
    marker={"size": 10},
    hovertext=f"{new_critical_speed:.0f} RPM",
    name=f"Critical speed: {new_critical_speed:.0f} RPM"
)
trace05x = go.Scatter(
    x=data['data'][0]['x'],
    y=data['data'][0]['x'] * s / 60,  # Converting RPM to Hertz and then applying the muktplier s
    mode="lines",
    name="0.5n / sn",
)

campbell_fig.add_trace(point_critical_speed)
campbell_fig.add_trace(trace05x)

# Call the function to add the secondary y-axis
rd.add_secondary_yaxis(campbell_fig, values)

#adjusting the legend
campbell_fig.update_layout(
    legend=dict(yanchor="top", y=0.99, xanchor="left", x=0.01),
)
# Show the updatedvfigure
campbell_fig.show()

## Órbita força assíncrona

In [7]:
orbit_plot = rd.interactive_orbit_campbell_async(
    campbell_fig,
    A1_async,
    A1_async,
    1,
    0.5,
    initial_speed=2700
)
orbit_plot.show()